In [150]:
aois = ["Bab el-Mandeb Strait", "Cape of Good Hope", "Suez Canal"]
countries_of_interest = [
    "Iran",
    "United Arab Emirates",
    # "Qatar",
    # "Bahrain",
    "Oman",
    # "Iraq",
]
# ISO_COUNTRIES = [818, 887, 262, 232, 682, 400]
START_DATE = "2023-10-07"

In [2]:
%reload_ext autoreload
%autoreload 2
import logging

import os

import pandas as pd


from acled_conflict_analysis import visuals
from acled_conflict_analysis import analysis
from acled_conflict_analysis import extraction

from datetime import date

logger = logging.getLogger()
logging.basicConfig(format="%(asctime)s %(message)s", level=logging.INFO)

from plotnine import *

# Conflict in the Persian Gulf

This section examines how the conflict events in the Persian Gulf have progressed since the crisis started in October 7th. The analysis is conducted using data from ACLED. Data was collected for three countries - Iran, Oman and UAE.

## Insights

To match the conflict analysis with the maritime trade trends as [previously seen on this web-book](https://datapartnership.org/red-sea-monitoring/notebooks/ports/README.html), we aggregated the ACLED data to show weekly trends near the ports of interest. 

### Visualizing conflict in the Persian Gulf and Strait of Hormuz between October 7th 2023 and October 20th 2024

In [151]:
data = extraction.acled_api(
    email_address=os.environ.get("ACLED_EMAIL"),
    access_key=os.environ.get("ACLED_KEY"),
    countries=countries_of_interest,
    start_date=START_DATE,
    end_date=date.today().isoformat(),
)

c:\WBG\Anaconda3\envs\data-goods\Lib\site-packages\urllib3\connectionpool.py:1103: InsecureRequestWarning: Unverified HTTPS request is being made to host 'api.acleddata.com'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings


In [153]:
analysis.data_type_conversion(data)

In [194]:
# Filter the rows where 'notes' column contains either 'Strait' or 'vessel'
strait_of_hormuz_attacks = data[
    (
        data["notes"].str.contains(
            r"\b(Strait|vessel|ship|tanker|Persian Gulf|boat|Houthi|Hormuz)",
            case=False,
            na=False,
        )
    )
    & (data["event_type"] != "Protests")
]
strait_of_hormuz_attacks.shape

C:\Users\wb588851\AppData\Local\Temp\ipykernel_47272\1639198041.py:2: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.


(13, 19)

In [195]:
data.drop_duplicates(inplace=True)

In [196]:
grouped_data = analysis.convert_to_gdf(
    strait_of_hormuz_attacks.groupby(
        [
            "latitude",
            "longitude",
            "notes",
            "event_type",
            "location",
            "country",
            "event_date",
        ]
    )["fatalities"]
    .agg(["sum", "count"])
    .reset_index()
)
grouped_data.rename(columns={"sum": "nrFatalities", "count": "nrEvents"}, inplace=True)

In [197]:
def split_in_three(text):
    # Step 1: Find the length of the text and divide into thirds
    third = len(text) // 3

    # Step 2: Find the closest space to the first third
    if " " in text[third:]:
        first_split_point = third + text[third:].find(" ")
    elif " " in text[:third]:
        first_split_point = text[:third].rfind(" ")
    else:
        first_split_point = third  # If no spaces, just split at third point

    # Step 3: Find the closest space to the second third
    if " " in text[first_split_point + third :]:
        second_split_point = (
            first_split_point + third + text[first_split_point + third :].find(" ")
        )
    elif " " in text[first_split_point:]:
        second_split_point = first_split_point + text[first_split_point:].rfind(" ")
    else:
        second_split_point = (
            first_split_point + third
        )  # If no spaces, just split at second third point

    # Step 4: Return the three parts
    return (
        text[:first_split_point],
        text[first_split_point:second_split_point],
        text[second_split_point:],
    )


# Apply the split_in_three function to the 'notes' column
grouped_data[["notes_part1", "notes_part2", "notes_part3"]] = (
    grouped_data["notes"].apply(lambda x: split_in_three(x)).apply(pd.Series)
)

In [198]:
m = grouped_data[grouped_data["event_type"] != "Protests"].explore(
    column="nrEvents",
    zoom_start=5.1,
    marker_kwds={"radius": 5},
    vmin=1,
    vmax=50,
    cmap="viridis",
    tooltip=["event_date", "location", "notes_part1", "notes_part2", "notes_part3"],
    tooltip_kwds={"aliases": ["date", "location", "details", "", ""]},
)
m

**There were 13 incidents in Oman and Iran revolving around vessels, ships, Houthi forces, boats or tankers since October 7th 2023.** These include events on the Arabian Sea, the Persian Gulf, Strait of Hormuz and Lake Tharthar. There was one incident in Kargan (a city in Iran) that resulted in 3 fatalities which involved the arest of fuel smugglers. Of the 28 incident, 4 involved fuel smuggling. 3 events were in the Persian Gulf, 2 in Gulf of Oman and 1 in Strait of Hormuz. 

In [199]:
conflict_by_country = analysis.get_acled_by_group(
    strait_of_hormuz_attacks, ["country"], freq="W"
)
conflict_by_location = analysis.get_acled_by_group(
    strait_of_hormuz_attacks, ["location"], freq="W"
)

In [208]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.palettes import Category10
from datetime import datetime

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

measure = "nrEvents"
location_types = list(conflict_by_location["location"].unique())

if len(location_types) < 10:
    # If there are fewer than 10 event types, randomly pick that many colors from Category10[10]
    colors = random.sample(Category10[10], num_event_types)
else:
    # If there are 10 or more event types, use Category10[10] directly
    colors = Category10[10]

show(
    visuals.get_stacked_bar_chart(
        conflict_by_location,
        f"{measure_names[measure]} across Locations in Iran and Oman",
        f"Source: ACLED. Accessed date {datetime.today().date().isoformat()}",
        date_column="event_date",
        categories=location_types,
        measure=measure,
        category_column="location",
        colors=colors,
        # events_dict=events_dict
    )
)

Loading BokehJS ...